# Traffic Incident Reports in San Francisco

Visualize traffic incident reports in San Francisco.

Data sources:

* [Police Department Incident Reports in San Francisco](https://data.sfgov.org/Public-Safety/Police-Department-Incident-Reports-2018-to-Present/wg3w-h783/data)
    - csv: https://data.sfgov.org/resource/wg3w-h783.csv
* [Traffic Signals in San Francisco](https://data.sfgov.org/Transportation/Traffic-Signals/ybh5-27n2)
    - csv: https://data.sfgov.org/resource/c8ue-f4py.csv
* [San Francisco Congestion Roads](https://cartovl.carto.com/dataset/sfcta_congestion_roads)
    - hosted in CARTO

In [1]:
from cartoframes.auth import set_default_credentials, Credentials
from cartoframes.viz import Map, Layer, Legend, Source
from cartoframes.data import Dataset
import pandas

> If you have a CARTO account, you can set your credentials in the following cell. This allows you to upload the dataset and share the final visualization through your account.

In [2]:
# username = '' # <-- insert your username here
# api_key = ''# <-- insert your API key here

# credentials = Credentials(username, api_key)
# set_default_credentials(credentials)

## Load incident reports

Using pandas, we can read an external data source, which is converted to a dataframe. Let's see which columns we have:

In [3]:
incident_reports_df = pandas.read_csv('https://data.sfgov.org/resource/wg3w-h783.csv')
incident_reports_df.head()

incident_datetime            incident_date incident_time  \
0  2018-12-02T00:45:00.000  2018-12-02T00:00:00.000         00:45   
1  2018-12-01T20:30:00.000  2018-12-01T00:00:00.000         20:30   
2  2019-03-18T14:01:00.000  2019-03-18T00:00:00.000         14:01   
3  2019-03-20T08:00:00.000  2019-03-20T00:00:00.000         08:00   
4  2019-03-12T13:30:00.000  2019-03-12T00:00:00.000         13:30   

   incident_year incident_day_of_week          report_datetime       row_id  \
0           2018               Sunday  2018-12-02T01:56:00.000  74374327130   
1           2018             Saturday  2018-12-01T21:18:00.000  74370071000   
2           2019               Monday  2019-03-18T14:21:00.000  78164004134   
3           2019            Wednesday  2019-03-20T14:06:00.000  78169706244   
4           2019              Tuesday  2019-03-15T18:02:00.000  78154706372   

   incident_id  incident_number   cad_number  ...  \
0       743743        180908554  183360210.0  ...   
1       743700        180908112  183353564.0  ...   
2       781640        190194129  190772267.0  ...   
3       781697        190199583  190792201.0  ...   
4       781547        196055103          NaN  ...   

                incident_description            resolution  \
0      Burglary Tools, Possession Of  Cite or Arrest Adult   
1                      Lost Property        Open or Active   
2                            Battery  Cite or Arrest Adult   
3  Theft, From Locked Vehicle, >$950        Open or Active   
4    Theft, Other Property, $50-$200        Open or Active   

                  intersection         cnn police_district  \
0          04TH ST \ JESSIE ST  24635000.0        Southern   
1      POWELL ST \ OFARRELL ST  24904000.0         Central   
2        22ND ST \ POTRERO AVE  23967000.0         Mission   
3  JESSIE EAST ST \ MISSION ST  35047000.0        Southern   
4                          NaN         NaN         Central   

            analysis_neighborhood supervisor_district   latitude   longitude  \
0  Financial District/South Beach                 6.0  37.784908 -122.404795   
1                      Tenderloin                 3.0  37.786410 -122.408036   
2                         Mission                 9.0  37.756834 -122.406699   
3                 South of Market                 6.0  37.784007 -122.404865   
4                             NaN                 NaN        NaN         NaN   

                                  point  
0    (37.78490829943, -122.40479506276)  
1  (37.786409612811, -122.408036237445)  
2  (37.756833733806, -122.406699002688)  
3   (37.78400661242, -122.404864795177)  
4                                   NaN  

[5 rows x 26 columns]

In [4]:
incident_reports_df.columns

Index(['incident_datetime', 'incident_date', 'incident_time', 'incident_year',
       'incident_day_of_week', 'report_datetime', 'row_id', 'incident_id',
       'incident_number', 'cad_number', 'report_type_code',
       'report_type_description', 'filed_online', 'incident_code',
       'incident_category', 'incident_subcategory', 'incident_description',
       'resolution', 'intersection', 'cnn', 'police_district',
       'analysis_neighborhood', 'supervisor_district', 'latitude', 'longitude',
       'point'],
      dtype='object')

Some of the `latitude` and `longitude` values are `NaN`, in the next step we get rid of them. After that, we create a dataset from the dataframe and use it in a Layer to visualize the data:

In [5]:
incident_reports_df = incident_reports_df[incident_reports_df.longitude == incident_reports_df.longitude]
incident_reports_df = incident_reports_df[incident_reports_df.latitude == incident_reports_df.latitude]

incident_reports_data = Dataset(incident_reports_df)

Map(Layer(incident_reports_data))

Now, we are going to use a **helper method** to color by category, and the category is 'Day of Week' (`incident_day_of_week`)

In [6]:
from cartoframes.viz.helpers import color_category_layer

Map(
    color_category_layer(incident_reports_data, 'incident_day_of_week', 'Day of Week', top=7)
)

As we can see in the legend, the days are sorted by frequency, which means that there're less incidents on Thursdays and More on Tuesdays. Since our purpose is not to visualize the frequency and we want to see the days properly sorted from Monday to Sunday in the legend, we can modify the helper and set the categories we want to visualize in the desired position:

In [7]:
from cartoframes.viz.helpers import color_category_layer

Map(
    color_category_layer(incident_reports_data, 'incident_day_of_week', 'Day of Week', cat=[
        'Monday',
        'Tuesday',
        'Wednesday',
        'Thursday',
        'Friday',
        'Saturday',
        'Sunday'
    ])
)

Now, we want to look for traffic incidents, and then use these categories to visualize those incidents:

In [8]:
incident_reports_df.incident_category.unique()

array(['Other Miscellaneous', 'Lost Property', 'Assault', 'Larceny Theft',
       'Disorderly Conduct', 'Robbery', 'Non-Criminal',
       'Malicious Mischief', 'Recovered Vehicle', 'Drug Offense',
       'Burglary', 'Suspicious Occ', 'Traffic Collision', 'Warrant',
       'Arson', 'Offences Against The Family And Children',
       'Traffic Violation Arrest', 'Forgery And Counterfeiting',
       'Missing Person', 'Motor Vehicle Theft', 'Case Closure',
       'Weapons Carrying Etc', 'Other', 'Weapons Offense', 'Fraud',
       'Civil Sidewalks', 'Other Offenses', 'Stolen Property',
       'Miscellaneous Investigation', 'Prostitution', 'Juvenile Offenses',
       'Homicide', 'Vandalism', 'Sex Offense', 'Courtesy Report',
       'Family Offense'], dtype=object)

In [9]:
from cartoframes.viz.helpers import size_category_layer

Map(
    size_category_layer(
        incident_reports_data,
        'incident_category',
        'Traffic Incidents',
        cat=['Traffic Collision', 'Traffic Violation Arrest'])
)

In CARTO we have a dataset we can use for the next step, named 'sfcta_congestion_roads'. We are going to set the `Credentials` for this dataset. To have more control over this dataset, if you have a CARTO account you can import it to have everything together, and it won't be needed to create a different source for this Dataset.

Once we've the data source created, we're going to combine two helper methods. The first one uses the Source with the roads data from CARTO, and the second one the traffic incident reports.

In [10]:
from cartoframes.viz.helpers import color_continuous_layer

sfcta_congestion_roads_source=Source(
    'sfcta_congestion_roads',
    Credentials(
        base_url='https://cartovl.carto.com',
        api_key='default_public'
    )
)

Map([
    color_continuous_layer(sfcta_congestion_roads_source, 'auto_speed', 'Recorded vehicle speeds'),
    size_category_layer(
        incident_reports_data,
        'incident_category',
        'Traffic Incidents',
        cat=['Traffic Collision', 'Traffic Violation Arrest'])
])

We are going to add information about traffic signals, by getting data from a different source:

In [11]:
traffic_signals_df = pandas.read_csv('https://data.sfgov.org/resource/c8ue-f4py.csv')
traffic_signals_df.head()

objectid       cnn          code     cnn_1   street1      street2  \
0     14201  23163000      CALTRANS  23163000  21ST AVE        SLOAT   
1     13946  23799001  MESSAGE SIGN  23799001   03RD ST         KING   
2     14161   1278800   Speed Radar   1278800   MADRONE   ULLOA - WB   
3     13949   7210000      CALTRANS   7210000   ALEMANY  CUT THROUGH   
4     13198  26528000           Fix  26528000   OCTAVIA         PINE   

  detection street3 sup_dist street4  ...         last_edited_date  \
0       NaN     NaN      4,7     NaN  ...  2019-04-18T14:45:34.000   
1                          6          ...  2019-04-18T14:45:34.000   
2                          7          ...  2019-04-18T14:45:34.000   
3                          9          ...  2019-04-18T14:45:34.000   
4                        2,5          ...  2019-04-18T14:45:13.000   

                                       point point_address point_zip  \
0  POINT (-122.477080829761 37.734617663245)           NaN       NaN   
1   POINT (-122.392013643268 37.77809930415)           NaN       NaN   
2  POINT (-122.467683831285 37.741501987719)           NaN       NaN   
3  POINT (-122.407917735682 37.737729505444)           NaN       NaN   
4  POINT (-122.427059672706 37.788786895296)           NaN       NaN   

  point_city point_state :@computed_region_6qbp_sg9q  \
0        NaN         NaN                        40.0   
1        NaN         NaN                        34.0   
2        NaN         NaN                        46.0   
3        NaN         NaN                        83.0   
4        NaN         NaN                       102.0   

  :@computed_region_qgnn_b9vv :@computed_region_26cr_cadq  \
0                        10.0                         8.0   
1                         1.0                        10.0   
2                        10.0                         8.0   
3                         2.0                         2.0   
4                         4.0                        11.0   

  :@computed_region_ajp5_b2md  
0                        35.0  
1                         4.0  
2                        41.0  
3                        25.0  
4                        30.0  

[5 rows x 61 columns]

In [12]:
traffic_signals_df.columns

Index(['objectid', 'cnn', 'code', 'cnn_1', 'street1', 'street2', 'detection',
       'street3', 'sup_dist', 'street4', 'sig_num', 'type', 'ic_make', 'model',
       'cabinet_si', 'system_num', 'master', 'bbs', 'veh_actuat', 'ped_signal',
       'ped_actuat', 'manual_con', 'tbc', 'interconne', 'preempt_pr',
       'd_ate2070', 'project_ne', 'project_ol', 'upgraded', 'yr_of_cont',
       'last_upgra', 'new_signal', 'mod_projec', 'full_upgra', 'beacon_fla',
       'funding', 'rlcam', 'startyear', 'caltrans_r', 'caltrans', 'percent_c',
       'sf', 'percent_sf', 'percent_po', 'lamp_assgn', 'lamp_sort', 'sort_me',
       'aps', 'created_user', 'created_date', 'last_edited_user',
       'last_edited_date', 'point', 'point_address', 'point_zip', 'point_city',
       'point_state', ':@computed_region_6qbp_sg9q',
       ':@computed_region_qgnn_b9vv', ':@computed_region_26cr_cadq',
       ':@computed_region_ajp5_b2md'],
      dtype='object')

In [13]:
traffic_signals_df = traffic_signals_df.rename(columns={'type': 'signal_type'})
traffic_signals_df.signal_type.unique()

array(['CALTRANS - HAWK', 'MESSAGE SIGN', 'RADAR SPEED SIGN', 'CALTRANS',
       'SIGNAL', 'BEACON - RRFB', 'PENDING SIGNAL', 'BEACON',
       'FUTURE SIGNAL', 'CALTRANS (BY CONTRACTOR CONSORTIUM GLC)',
       'PENDING BEACON', 'OTHER', 'LANE CONTROL', 'FLASHER',
       'LIGHTED CROSSWALK', 'DALY CITY'], dtype=object)

Since there is no `latitude` and `longitude` columns, we can use the `point` column to create a [GeoDataFrame](https://geopandas.readthedocs.io/en/latest/gallery/create_geopandas_from_pandas.html).

In [14]:
import geopandas
from shapely import wkt

traffic_signals_df['point'] = traffic_signals_df['point'].apply(wkt.loads)
traffic_signals_df = traffic_signals_df.rename(columns={'point': 'geometry'}).set_geometry('geometry')
trafic_signals_gdf = geopandas.GeoDataFrame(traffic_signals_df, geometry='geometry')

In [15]:
traffic_signals_data = Dataset(trafic_signals_gdf)

Map(Layer(traffic_signals_data))

We are getting only the signal types we want to visualize, but we are going to build a Layer that uses cross symbols this time:

In [16]:
signal_gdf = trafic_signals_gdf[trafic_signals_gdf['signal_type'].isin(['RADAR SPEED SIGN', 'FLASHER',  'LIGHTED CROSSWALK'])]
signal_data = Dataset(signal_gdf)

Map(
    Layer(
        signal_data,
        '''
        color: ramp($signal_type, bold)
        width: 15
        symbol: cross
        ''',
        legend={
           'type': 'color-category',
           'title': 'Radar'
        })
)

All together:

In [17]:
Map([
    color_continuous_layer(
        sfcta_congestion_roads_source, 'auto_speed', 'Recorded vehicle speeds'),
    size_category_layer(
        incident_reports_data, 
        'incident_category',
        'Traffic Incidents',
        cat=['Traffic Collision', 'Traffic Violation Arrest']),
    Layer(
        signal_data,
        '''
        color: ramp($signal_type, bold)
        width: 15
        symbol: cross
        ''',
        legend={
           'type': 'color-category',
           'title': 'Radar'
        })
])